
# Change the seed of a DOE

[Latin hypercube sampling](https://en.wikipedia.org/wiki/Latin_hypercube_sampling)_
is an example of stochastic DOE algorithm:
given an input dimension and a number of samples,
running the algorithm twice will give two different DOEs.

For the sake of reproducibility,
|g| uses a [random seed](https://en.wikipedia.org/wiki/Random_seed)_:
given an input dimension, a number of samples and a random seed,
running the algorithm twice will give the same DOE.

In this example,
we will see how |g| uses the random seed
and how the user can change its value.


In [ ]:
from __future__ import annotations

from gemseo import create_design_space
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo import execute_algo
from gemseo.algos.doe.lib_openturns import OpenTURNS
from gemseo.algos.opt_problem import OptimizationProblem
from gemseo.core.mdofunctions.mdo_function import MDOFunction

## At the scenario level
First,
we illustrate the use of the random seed at the :class:`.DOEScenario` level
which is the appropriate level for most users.
Then,
we will illustrate this use at the :class:`.OptimizationProblem` level
which can be useful for developers.

Let us consider an :class:`.MDODiscipline` representing the function $y=x^2$:



In [ ]:
discipline = create_discipline("AnalyticDiscipline", expressions={"y": "x**2"})

This function is defined over the interval $[-1,1]$:



In [ ]:
design_space = create_design_space()
design_space.add_variable("x", l_b=-1, u_b=1)

We want to sample this discipline over this design space.
For that,
we express the sampling problem as a :class:`.DOEScenario`:



In [ ]:
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "y", design_space, scenario_type="DOE"
)

and solve it:



In [ ]:
scenario.execute({"algo": "OT_OPT_LHS", "n_samples": 2})
scenario.formulation.opt_problem.database.get_last_n_x_vect(2)

You can get the value of the random seed that has been used:



In [ ]:
scenario._lib.seed

When using the same DOE algorithm,
a new call to :meth:`.DOEScenario.execute` increments the :attr:`.DOELibrary.seed`.
Then,
solving again this problem with the same configuration leads to a new result:



In [ ]:
scenario.execute({"algo": "OT_OPT_LHS", "n_samples": 2})
scenario.formulation.opt_problem.database.get_last_n_x_vect(2)

and we can check that the value of the seed was incremented:



In [ ]:
scenario._lib.seed

You can also pass a custom ``"seed"`` to the DOE algorithm
with the key ``"algo_options"`` of the ``input_data``
passed to :meth:`.DOEScenario.execute`:



In [ ]:
scenario.execute({"algo": "OT_OPT_LHS", "n_samples": 2, "algo_options": {"seed": 123}})
scenario.formulation.opt_problem.database.get_last_n_x_vect(2)

You can verify that :attr:`.DOELibrary.seed` has not been replaced by the custom value
but incremented:



In [ ]:
scenario._lib.seed

## At the problem level
Basic
~~~~~
Let us consider an :class:`.MDOFunction` representing the function $y=x^2$:



In [ ]:
function = MDOFunction(lambda x: x**2, "f", input_names=["x"], output_names=["y"])

and defined over the unit interval $x\in[0,1]$:



In [ ]:
design_space = create_design_space()
design_space.add_variable("x", l_b=-1, u_b=1)

We want to sample this function over this design space.
For that,
we express the sampling problem as an :class:`.OptimizationProblem`:



In [ ]:
problem = OptimizationProblem(design_space)
problem.objective = function

and solve it:



In [ ]:
execute_algo(problem, "OT_OPT_LHS", algo_type="doe", n_samples=2)
problem.database.get_last_n_x_vect(2)

Note:
    We use the function :func:`.execute_algo`
    as the :class:`.OptimizationProblem` does not have a method :func:`execute`
    unlike the :class:`.Scenario`.

Solving again this problem with the same configuration leads to the same result:



In [ ]:
execute_algo(problem, "OT_OPT_LHS", algo_type="doe", n_samples=2)
problem.database.get_last_n_x_vect(2)

and the result is still the same if we take 1 as random seed,
as 1 is the default value of this seed:



In [ ]:
execute_algo(problem, "OT_OPT_LHS", algo_type="doe", n_samples=2, seed=1)
problem.database.get_last_n_x_vect(2)

If you want to use a different random seed,
you only have to change the value of ``seed``:



In [ ]:
execute_algo(problem, "OT_OPT_LHS", algo_type="doe", n_samples=2, seed=3)
problem.database.get_last_n_x_vect(2)

### Advanced
You can also solve your problem with a lower level API
by directly instantiating the :class:`.DOELibrary` of interest.
A :class:`.DOELibrary` has a :attr:`~.DOELibrary.seed` initialized at 0
that is incremented at the beginning of each execution:



In [ ]:
library = OpenTURNS()
library.algo_name = "OT_OPT_LHS"
library.execute(problem, n_samples=2)
library.seed, problem.database.get_last_n_x_vect(2)

Solving again the problem will give different samples:



In [ ]:
library.execute(problem, n_samples=2)
library.seed, problem.database.get_last_n_x_vect(2)

You can also change the seed:



In [ ]:
library.seed = 123
library.execute(problem, n_samples=2)
library.seed, problem.database.get_last_n_x_vect(2)